### Preperation

In [ ]:
import message_ix
import ixmp

import numpy as np
import pandas as pd
import pyam
import matplotlib.pyplot as plt 

In [ ]:
mp = ixmp.Platform()

In [ ]:
# Import the results of the three scenarios to compare

# baseline_DEFAULT, 2 degrees, the MESSAGEix-GLOBIOM 1.1-R12 baseline 
# Previous scenarios: 'baseline_DEFAULT_1207_3_macro' and '2degrees_1207_3'
# Submission 1 Paper Scenarios: baseline_DEFAULT_test_0310_macro, 2degrees_test_0310_macro
# High carbon price scenarios: high_ctax_steel_update_1902 
# Submission 2 Paper Scenarios: 'baseline_DEFAULT_update_2207_2025_macro', '2degrees_2207_2025_macro' 

model1_name = 'MESSAGEix-Materials'
scen1_name = 'baseline_DEFAULT_update_2207_2025_macro'
scen2_name = '2degrees_2207_2025_macro'

model2_name = 'MESSAGEix-GLOBIOM 1.1-R12'
scen3_name = 'baseline_DEFAULT'
version_3 = 7 

scen1 = message_ix.Scenario(mp, model1_name ,scen1_name, cache=True)
scen2 = message_ix.Scenario(mp, model1_name, scen2_name, cache=True)
scen3 = message_ix.Scenario(mp, model2_name ,scen3_name, version = version_3, cache=True)

In [ ]:
# Move the year 2020 to 2 degrees scenario. Perform this step only once. 

# timeseries1 = scen1.timeseries()
# timeseries1_2020=timeseries1[timeseries1['year']==2020]

# scen2.check_out(timeseries_only = True)
# scen2.add_timeseries(timeseries1_2020)
# scen2.commit('year 2020 added.')

In [ ]:
timeseries1 = scen1.timeseries()
timeseries2 = scen2.timeseries()
timeseries3 = scen3.timeseries()
timeseries_final = pd.concat([timeseries1, timeseries2, timeseries3])

In [ ]:
# Add hydrogen years 2020 and 2025

variables_1 = [

'Final Energy|Industry excl Non-Energy Use|Steel|Hydrogen',
'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Hydrogen',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Hydrogen',
'Final Energy|Industry excl Non-Energy Use|Chemicals|Hydrogen',
'Final Energy|Industry excl Non-Energy Use|Steel|Heat',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Heat',
'Final Energy|Industry|Steel|Hydrogen',
'Final Energy|Industry|Non-Metallic Minerals|Hydrogen',
'Final Energy|Industry|Non-Ferrous Metals|Hydrogen',
# 'Final Energy|Industry|Chemicals|Hydrogen',   
'Final Energy|Industry excl Non-Energy Use|Chemicals|Heat',
# 'Final Energy|Industry excl Non-Energy Use|Solar',

        ]


scenarios =  []
scenarios.append(scen1_name)
scenarios.append(scen2_name)

for v in variables_1: 
    for r in timeseries_final['region'].unique():
        if r == 'CPA':
            continue
        for s in scenarios:
            df_add = pd.DataFrame (
            {'region': r,
             'variable': v,
             'unit': 'EJ/yr',
             'year': [2020, 2025],
             'value': 0,
             'model': 'MESSAGEix-Materials',
             'scenario': s
             })
            
            timeseries_final = pd.concat([timeseries_final,df_add])

variables_2 = [
    'Final Energy|Industry excl Non-Energy Use|Other Sector|Hydrogen',
    'Final Energy|Industry excl Non-Energy Use|Hydrogen'   
    
]            

for v in variables_2:
    for r in timeseries_final['region'].unique():
        if r == 'CPA':
            continue
        for s in scenarios:
            df_add_2 = pd.DataFrame (
            {'region': r,
             'variable': v ,
             'unit': 'EJ/yr',
             'year': [2020],
             'value': 0,
             'model': 'MESSAGEix-Materials',
             'scenario': s
             })

            timeseries_final = pd.concat([timeseries_final,df_add_2])
                      
timeseries_final = timeseries_final.drop_duplicates()
timeseries_final = timeseries_final.reset_index(drop=True)

# Show duplicates
timeseries_final[timeseries_final.duplicated()]

In [ ]:
df = pyam.IamDataFrame(data=timeseries_final)
df.filter(year= [2020,2025,2030,2035, 2040, 2045, 2050, 2055, 2060,2070], inplace = True)

### Primary Energy

In [ ]:
variable_list = ['Primary Energy|Solar',
                 'Primary Energy|Wind', 
                 'Primary Energy|Other',
                 'Primary Energy|Oil',
                 'Primary Energy|Ocean',
                 'Primary Energy|Nuclear',
                 'Primary Energy|Hydro',
                 'Primary Energy|Geothermal',
                 'Primary Energy|Gas',
                 'Primary Energy|Coal',
                 'Primary Energy|Biomass']

df.filter(variable='Primary Energy', region='GLB region (R12)').plot()
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack()
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack()

In [ ]:
variable_list = ['Primary Energy|Solar',
                 'Primary Energy|Wind', 
                 'Primary Energy|Other',
                 'Primary Energy|Oil',
                 'Primary Energy|Ocean',
                 'Primary Energy|Nuclear',
                 'Primary Energy|Hydro',
                 'Primary Energy|Geothermal',
                 'Primary Energy|Gas',
                 'Primary Energy|Coal',
                 'Primary Energy|Biomass']


pyam.run_control().update(
    {'color': {'variable': { 
                "Primary Energy|Solar": 'orange',
                 'Primary Energy|Wind': 'cornflowerblue',
                 'Primary Energy|Other': "grey",
                 'Primary Energy|Oil': "blue",
                 'Primary Energy|Ocean': "darkblue",
                 'Primary Energy|Nuclear': 'maroon',
                 'Primary Energy|Hydro': 'deepskyblue',
                 'Primary Energy|Geothermal': 'mediumaquamarine',
                 'Primary Energy|Gas': 'lightseagreen',
                 'Primary Energy|Coal': 'darkslategrey',
                 'Primary Energy|Biomass': 'cadetblue'
 }}}
)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=5)

df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack(ax=ax1)
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack(ax=ax2)

ax2.legend(
      [
      "Wind",
       "Solar",
       "Other",
       "Oil",
       "Ocean",
       "Nuclear",
       "Hydro",
       "Geothermal",
       "Gas",
       "Coal",
       "Biomass"   
      ],
      bbox_to_anchor=(1.6, 0.1),
      loc="lower right",
  )

ax1.set_ylim(0, 940)
ax2.set_ylim(0,940)

ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid() 

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax2.set_title("2degrees", fontdict={'fontsize':16})

fig.savefig('primary_energy_2307.jpg', bbox_inches='tight')

### CO2 Emissions

In [ ]:
df.filter(variable='Emissions|CO2', region='GLB region (R12)').plot()

### CO2 Emissions (from thermal energy needs) by Industry Sector

In [ ]:
variable_list = [

'Emissions|CO2|Energy|Demand|Industry|Chemicals|Ammonia', 
'Emissions|CO2|Energy|Demand|Industry|Chemicals|Methanol',
'Emissions|CO2|Energy|Demand|Industry|Chemicals|High Value Chemicals',
# 'Emissions|CO2|Energy|Demand|Industry|Non-Ferrous Metals|Aluminium',
# 'Emissions|CO2|Energy|Demand|Industry|Non-Metallic Minerals|Cement',
# 'Emissions|CO2|Energy|Demand|Industry|Other Sector', 
# 'Emissions|CO2|Energy|Demand|Industry|Steel' 
]


pyam.run_control().update(
    {'color': {'variable': { 
                 'Emissions|CO2|Energy|Demand|Industry|Chemicals|High Value Chemicals': 'olive' ,
                 'Emissions|CO2|Energy|Demand|Industry|Chemicals|Ammonia': 'black',
                 'Emissions|CO2|Energy|Demand|Industry|Chemicals|Methanol': 'slategray',
 }}}
)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=5)

df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack(ax=ax1)
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack(ax=ax2)

ax2.legend(
      [
       'Methanol',
       'Ammonia',
       'High Value Chemicals',
      ],
      bbox_to_anchor=(1.6, 0.1),
      loc="lower right",
  )

ax1.set_ylim(-2500, 1800)
ax2.set_ylim(-2500,1800)

ax1.set_title("2 degrees - high demand", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("MtCO2",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("2degrees - low demand", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("MtCO2", fontdict={'fontsize':16})

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid() 

fig.savefig('chemicals_emissions.jpg', bbox_inches='tight')

### CO2 Emissions (industrial processes) by Industry Sector

In [ ]:
variable_list = [

'Emissions|CO2|Industrial Processes|Non-Ferrous Metals',
'Emissions|CO2|Industrial Processes|Non-Metallic Minerals|Cement'

]

df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack()
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack()

### CO2 Emissions by end-use sector (industr,res-com, transport)

In [ ]:
industry_total = ["Emissions|CO2|Energy|Demand|Industry", "Emissions|CO2|Industrial Processes"]

df.aggregate(
    "Emissions|CO2|Industry", components=industry_total, append=True,
)

all_emissions = [ "Emissions|CO2|Energy|Demand|Transportation", 
                 "Emissions|CO2|Energy|Demand|Residential and Commercial and AFOFI",
                 "Emissions|CO2|Industry"
                ]

pyam.run_control().update(
    {'color': {'variable': {"Emissions|CO2|Energy|Demand|Transportation": "gray",
                            "Emissions|CO2|Energy|Demand|Residential and Commercial and AFOFI": "teal",
                            "Emissions|CO2|Industry": "olive"                                           
                           }}}
)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=5)

df.filter(variable= all_emissions, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack(ax=ax1)
df.filter(variable= all_emissions, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack(ax=ax2)

ax2.legend(
      [ "Industry",
       "Transportation", 
       "Residential and Commercial and AFOFI",  
      ],
      bbox_to_anchor=(1.75, 0.1),
      loc="lower right",
  )

ax1.set_ylim(0, 35000)
ax2.set_ylim(0,35000)

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("MtCO2/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("MtCO2/yr", fontdict={'fontsize':16})

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid() 

fig.savefig('direct_co2_end_uses_2307.jpg', bbox_inches='tight')

### CO2 Total Emissions

Below cell can only be run once.

In [ ]:
cement_total = ['Emissions|CO2|Energy|Demand|Industry|Non-Metallic Minerals|Cement', 
                'Emissions|CO2|Industrial Processes|Non-Metallic Minerals|Cement']

aluminum_total = ['Emissions|CO2|Energy|Demand|Industry|Non-Ferrous Metals', 
                  'Emissions|CO2|Industrial Processes|Non-Ferrous Metals'] 



df.aggregate(
    "Emissions|CO2|Industry|Non-Ferrous Metals|Aluminium", components=aluminum_total, append=True,
)

df.aggregate(
    "Emissions|CO2|Industry|Non-Metallic Minerals|Cement", components=cement_total, append=True,
)

all_emissions = ['Emissions|CO2|Energy|Demand|Industry|Chemicals|Ammonia', 
                 'Emissions|CO2|Energy|Demand|Industry|Chemicals|High Value Chemicals',
                 'Emissions|CO2|Energy|Demand|Industry|Chemicals|Methanol',
                 "Emissions|CO2|Industry|Non-Ferrous Metals|Aluminium",
                 "Emissions|CO2|Industry|Non-Metallic Minerals|Cement",
                 'Emissions|CO2|Energy|Demand|Industry|Other Sector', 
                 'Emissions|CO2|Energy|Demand|Industry|Steel',
                ]


pyam.run_control().update(
    {'color': {'variable': { 'Emissions|CO2|Energy|Demand|Industry|Other Sector': 'darkorange',
                'Emissions|CO2|Energy|Demand|Industry|Steel': 'burlywood',
                 'Emissions|CO2|Energy|Demand|Industry|Chemicals|High Value Chemicals': 'olive' ,
                 'Emissions|CO2|Energy|Demand|Industry|Chemicals|Ammonia': 'black',
                 'Emissions|CO2|Energy|Demand|Industry|Chemicals|Methanol': 'slategray',
                 "Emissions|CO2|Industry|Non-Ferrous Metals|Aluminium": 'darkseagreen'  ,
                 "Emissions|CO2|Industry|Non-Metallic Minerals|Cement": 'peru' }}}
)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=5)

df.filter(variable= all_emissions, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack(ax=ax1)
df.filter(variable= all_emissions, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack(ax=ax2)

ax2.legend(
      ['Cement',
       'Aluminum',
       'Steel',
       'Other Sector',
       'Methanol',
       'High Value Chemicals',
       'Ammonia',
      ],
      bbox_to_anchor=(1.6, 0.1),
      loc="lower right",
  )

ax1.set_ylim(-5000, 18000)
ax2.set_ylim(-5000,18000)

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("MtCO2/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("MtCO2/yr", fontdict={'fontsize':16})

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid() 

fig.savefig('direct_co2industry_2307.jpg', bbox_inches='tight')

### Kyoto Emissions

In [ ]:
df.filter(variable='Emissions|Kyoto Gases', region='GLB region (R12)').plot()

### Final Energy - Total

In [ ]:
# Total

variable_list = ['Final Energy|Solar',
                 'Final Energy|Hydrogen',
                 'Final Energy|Heat',
                 'Final Energy|Solids|Biomass',
                 'Final Energy|Solids|Coal',
                 'Final Energy|Liquids|Biomass',
                 'Final Energy|Liquids|Coal',
                 'Final Energy|Liquids|Gas',
                 'Final Energy|Liquids|Oil',
                 'Final Energy|Geothermal',
                 'Final Energy|Gases',
                 'Final Energy|Electricity']

df.filter(variable='Final Energy', region='GLB region (R12)').plot()
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack()
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack()

### Final Energy by Industry 

In [ ]:
variable_list = ['Final Energy|Industry|Other Sector',
                'Final Energy|Industry|Steel',
                 'Final Energy|Industry|Chemicals|High Value Chemicals',
                 'Final Energy|Industry|Chemicals|Ammonia',
                 'Final Energy|Industry|Chemicals|Methanol',
                 'Final Energy|Industry|Non-Ferrous Metals',
                 'Final Energy|Industry|Non-Metallic Minerals',
                ]


fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

pyam.run_control().update(
    {'color': {'variable': { 'Final Energy|Industry|Other Sector': 'darkorange',
                'Final Energy|Industry|Steel': 'burlywood',
                 'Final Energy|Industry|Chemicals|High Value Chemicals': 'olive' ,
                 'Final Energy|Industry|Chemicals|Ammonia': 'black',
                 'Final Energy|Industry|Chemicals|Methanol': 'red',
                 'Final Energy|Industry|Non-Ferrous Metals': 'darkseagreen'  ,
                 'Final Energy|Industry|Non-Metallic Minerals': 'peru',}}}
)

df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack(ax=ax1)
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack(ax=ax2)

ax1.set_ylim(0,390)
ax2.set_ylim(0,390)

ax2.legend(
      ['Steel',
       'Other Sector',
       'Non-Metallic Minerals',
       'Non-Ferrous Metals',
       'Methanol',
       'High Value Chemicals',
       'Ammonia'
      ],
      bbox_to_anchor=(1.4, 0.1),
      loc="lower right",
  )

fig.suptitle('Final Energy by Industry Sector',fontsize=15)

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid() 

### Final Energy by end-use sector

In [ ]:
variable_list = ['Final Energy|Industry',
                 "Final Energy|Transportation",
                 "Final Energy|Residential and Commercial"
                ]

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=5)

pyam.run_control().update(
    {'color': {'variable': { 'Final Energy|Industry': 'olive',
                'Final Energy|Transportation': 'gray',
                "Final Energy|Residential and Commercial": "teal"
}}}
)

df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack(ax=ax1)
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack(ax=ax2)

ax1.set_ylim(0,750)
ax2.set_ylim(0,750)

ax2.legend(
      ["Transportation",
       "Residential and Commercial",
       "Industry"
      ],
      bbox_to_anchor=(1.75, 0.1),
      loc="lower right",
  )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid()

fig.savefig('final_energy_end_use_2307.jpg', bbox_inches='tight')

### Final Energy by Fuel (feedstock + energy)

In [ ]:
variable_list = [
                 'Final Energy|Industry|Solar',
                 'Final Energy|Industry|Hydrogen',
                 'Final Energy|Industry|Heat',
                 'Final Energy|Industry|Solids|Biomass',
                 'Final Energy|Industry|Solids|Coal',
                 'Final Energy|Industry|Liquids|Biomass',
                 'Final Energy|Industry|Liquids|Coal',
                 'Final Energy|Industry|Liquids|Gas',
                 'Final Energy|Industry|Liquids|Oil',
                 'Final Energy|Industry|Geothermal',
                 'Final Energy|Industry|Gases',
                 'Final Energy|Industry|Electricity',
                ]

df_graph_1 = df.copy()
df_graph_2 = df.copy()

pyam.run_control().update(
    {'color': {'variable': {'Final Energy|Industry|Solar': 'slategrey',
                 'Final Energy|Indsutry|Hydrogen': 'brown',
                 'Final Energy|Industry|Heat': 'deepskyblue',
                 'Final Energy|Industry|Solids|Biomass': 'cadetblue',
                 'Final Energy|Industry|Solids|Coal': 'orange',
                 'Final Energy|Industry|Liquids|Biomass': 'darkcyan',
                 'Final Energy|Industry|Liquids|Coal': 'darkslategrey',
                 'Final Energy|Industry|Liquids|Gas': 'lightseagreen',
                 'Final Energy|Industry|Liquids|Oil': 'blue',
                 'Final Energy|Industry|Geothermal': 'mediumaquamarine',
                 'Final Energy|Industry|Gases':'grey',
                 'Final Energy|Industry|Electricity':'seagreen',  
    }}}
)

years_filter = [2020,2025,2030,2035,2040,2045,2050,2055,2060,2070,2080,2090,2100]

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, 
                  year= years_filter, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, 
                  year= years_filter,inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

ax1.set_ylim(0,390)
ax2.set_ylim(0,390)

ax2.legend(
     ['Solids|Coal',
      'Solids|Biomass', 
      'Solar',
      'Liquids|Oil',
      'Liquids|Gas',
      'Other',
      'Liquids|Biomass',
      'Hydrogen',
      'Heat',
      'Gas',
      'Electricity'
     ],
     bbox_to_anchor=(1.4, 0.1),
     loc="lower right",
 )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid() 

fig.suptitle('Final Energy Industry by Fuels, Global',fontsize=15)

fig.savefig('final_energy_by_fuel.jpg', bbox_inches='tight')

### Final Energy by Fuel (only energy)

In [ ]:
variable_list = [

'Final Energy|Industry excl Non-Energy Use|Electricity',
'Final Energy|Industry excl Non-Energy Use|Gases',
'Final Energy|Industry excl Non-Energy Use|Heat',
'Final Energy|Industry excl Non-Energy Use|Hydrogen',
'Final Energy|Industry excl Non-Energy Use|Liquids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Liquids|Coal',
'Final Energy|Industry excl Non-Energy Use|Liquids|Oil', 
'Final Energy|Industry excl Non-Energy Use|Solar',
'Final Energy|Industry excl Non-Energy Use|Solids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Solids|Coal',
    
]


df_graph_1 = df.copy()
df_graph_2 = df.copy()

pyam.run_control().update(
    {'color': {'variable': {'Final Energy|Industry excl Non-Energy Use|Solar': 'gold',
                 'Final Energy|Industry excl Non-Energy Use|Hydrogen': 'brown',
                 'Final Energy|Industry excl Non-Energy Use|Heat': 'olive',
                 'Final Energy|Industry excl Non-Energy Use|Solids|Biomass': 'seagreen',
                 'Final Energy|Industry excl Non-Energy Use|Solids|Coal': 'darkslategrey',
                 'Final Energy|Industry excl Non-Energy Use|Liquids|Biomass': 'greenyellow',
                 'Final Energy|Industry excl Non-Energy Use|Liquids|Coal': 'mediumaquamarine',
                 'Final Energy|Industry excl Non-Energy Use|Liquids|Oil': 'blue',
                 'Final Energy|Industry excl Non-Energy Use|Gases':'slategrey',
                 'Final Energy|Industry excl Non-Energy Use|Electricity':'lightblue',
    }}}
)

years_filter = [2020,2025,2030,2035,2040,2045,2050,2055,2060,2070,2080,2090,2100]

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, 
                  year= years_filter, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, 
                  year= years_filter,inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=5)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

ax2.legend(
     [
      'Coal',
      'Biomass', 
      'Solar',
      'Oil',
      'Methanol',
      'Ethanol',
      'Hydrogen', 
      'Heat',
      'Gas',
      'Electricity'
     ],
     bbox_to_anchor=(1.4, 0.1),
     loc="lower right",
 )

ax1.set_title("", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})

ax1.set_ylim(0,210)
ax2.set_ylim(0,210)

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid() 

fig.savefig('final_energy_by_fuel_excluding_2307.jpg', bbox_inches='tight')

### Non-Energy Use

In [ ]:
variable_list = [
    
'Final Energy|Non-Energy Use|Gases|Other',
'Final Energy|Non-Energy Use|Gases|Electricity',
'Final Energy|Non-Energy Use|Liquids|Biomass',
'Final Energy|Non-Energy Use|Liquids|Gas',
'Final Energy|Non-Energy Use|Liquids|Oil',
'Final Energy|Non-Energy Use|Solids|Biomass',
'Final Energy|Non-Energy Use|Solids|Coal',
'Final Energy|Non-Energy Use|Hydrogen',
   
]

df.subtract('Final Energy|Non-Energy Use|Gases', 'Final Energy|Non-Energy Use|Gases|Electricity', 
            'Final Energy|Non-Energy Use|Gases|Other',axis='variable', append = True)

region_list = df.region
region_list.remove('CPA')

for r in region_list: 
    df_graph_1 = df.copy()
    df_graph_2 = df.copy()

    df_graph_1.filter(variable= variable_list, region= r, model = model1_name, scenario = scen1_name, inplace = True)
    df_graph_2.filter(variable= variable_list, region= r, model = model1_name, scenario = scen2_name, inplace = True)

    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
    fig.tight_layout(pad=5)
    
    pyam.run_control().update(
    {'color': {'variable': {
                 'Final Energy|Non-Energy Use|Hydrogen': 'brown',
                 'Final Energy|Non-Energy Use|Solids|Biomass': 'seagreen',
                 'Final Energy|Non-Energy Use|Solids|Coal': 'darkslategrey',
                 'Final Energy|Non-Energy Use|Liquids|Biomass': 'greenyellow',
                 'Final Energy|Non-Energy Use|Liquids|Oil': 'blue',
                 'Final Energy|Non-Energy Use|Gases|Other':'slategrey',
                 'Final Energy|Non-Energy Use|Gases|Electricity':'lightblue',
                 'Final Energy|Non-Energy Use|Liquids|Gas': 'royalblue'
    }}}
    )

    df_graph_1.plot.stack(ax=ax1)
    df_graph_2.plot.stack(ax=ax2)

    ax2.legend(
         ['Coal',
          'Biomass',
          'Oil',
          'Ethane',
          'Ethanol',
          'Hydrogen',
          'Gas',
          'Electricity'
         ],
         bbox_to_anchor=(1.4, 0.1),
         loc="lower right",
     )

    ax1.set_title("", fontdict={'fontsize':16})
    ax1.set_xlabel("", fontdict={'fontsize':16})
    ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
    ax1.get_legend().remove()
    ax1.set_ylim(0,60)

    ax2.set_title("", fontdict={'fontsize':16})
    ax2.set_xlabel("", fontdict={'fontsize':16})
    ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
#     ax2.get_legend().remove()
    ax2.set_ylim(0,60)

    ax1.xaxis.grid() 
    ax1.yaxis.grid() 
    ax2.yaxis.grid() 
    ax2.xaxis.grid()
    
    name = "non_energy_use_feedstock_23_07_" + r + ".jpg"
    fig.savefig(name, bbox_inches='tight')

#### High Value Chemicals Final Energy (Feedstock)

In [ ]:
variable_list = [
    
"Final Energy|Non-Energy Use|Chemicals|High Value Chemicals|Liquids|Biomass",
"Final Energy|Non-Energy Use|Chemicals|High Value Chemicals|Liquids|Gas",
"Final Energy|Non-Energy Use|Chemicals|High Value Chemicals|Liquids|Oil",
"Final Energy|Non-Energy Use|Chemicals|High Value Chemicals|Other"

]

df_graph_1 = df.copy()
df_graph_2 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=5)

pyam.run_control().update(
    {'color': {'variable': {
                 "Final Energy|Non-Energy Use|Chemicals|High Value Chemicals|Other": 'mediumaquamarine',
                 "Final Energy|Non-Energy Use|Chemicals|High Value Chemicals|Liquids|Oil": 'blue',
                 "Final Energy|Non-Energy Use|Chemicals|High Value Chemicals|Liquids|Gas":'royalblue',
                 "Final Energy|Non-Energy Use|Chemicals|High Value Chemicals|Liquids|Biomass":'seagreen',
    }}}
)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

ax2.legend(
     ['Methanol',
      'Oil Products', 
      'Ethane',
      'Ethanol',
     ],
     bbox_to_anchor=(1.4, 0.1),
     loc="lower right",
 )

ax1.set_title("", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,28,5)

ax2.set_title("", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
ax2.set_ylim(0,28,5)

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid()

fig.savefig('high_value_chemicals_feedstock_2307.jpg', bbox_inches='tight')

#### Ammonia (Final Energy ALL) 

In [ ]:
variable_list = [

'Final Energy|Non-Energy Use|Chemicals|Ammonia|Gases|Other', 
'Final Energy|Non-Energy Use|Chemicals|Ammonia|Gases|Electricity', 
'Final Energy|Non-Energy Use|Chemicals|Ammonia|Liquids|Oil', 
'Final Energy|Non-Energy Use|Chemicals|Ammonia|Solids|Biomass',
'Final Energy|Non-Energy Use|Chemicals|Ammonia|Solids|Coal'

]

variable_ccs = ["Carbon Sequestration|CCS|Industry|Fossil|Chemicals|Ammonia", 
                "Carbon Sequestration|CCS|Industry|Biomass|Chemicals|Ammonia"]


new_var_ccs = ["Carbon Sequestration|CCS|Industry|Chemicals|Ammonia"]

df.subtract('Final Energy|Non-Energy Use|Chemicals|Ammonia|Gases', 
            'Final Energy|Non-Energy Use|Chemicals|Ammonia|Gases|Electricity', 
            'Final Energy|Non-Energy Use|Chemicals|Ammonia|Gases|Other',axis='variable', append = True)

df.aggregate(
    "Carbon Sequestration|CCS|Industry|Chemicals|Ammonia", components=variable_ccs, append=True,
)

df_graph_1 = df.copy()
df_graph_2 = df.copy()
df_graph_3 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)
df_graph_3.filter(variable= new_var_ccs, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
ax3 = ax2.twinx()
fig.tight_layout(pad=5)

pyam.run_control().update(
    {'color': {'variable': {
                 'Final Energy|Non-Energy Use|Chemicals|Ammonia|Gases|Other': 'slategrey',
                 'Final Energy|Non-Energy Use|Chemicals|Ammonia|Gases|Electricity': 'lightblue',
                 'Final Energy|Non-Energy Use|Chemicals|Ammonia|Liquids|Oil':'blue',
                 'Final Energy|Non-Energy Use|Chemicals|Ammonia|Solids|Biomass':'seagreen',
                 'Final Energy|Non-Energy Use|Chemicals|Ammonia|Solids|Coal': 'darkslategrey'
    }}}
)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)
df_graph_3.plot.line(ax=ax3, color='black', linewidth=5)

ax2.legend(
     ['Coal',
      'Biomass', 
      'Oil',
      'Gas',
      'Electricity'
     ],
     bbox_to_anchor=(1.55, 0.1),
     loc="lower right",
 )

ax3.legend(['CCS Use'],
     bbox_to_anchor=(1.55, 0.5),
     loc="lower right",)

ax1.set_title("No Policy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
# ax1.set_ylim(0,8,5)

ax2.set_title("2 degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
# ax2.set_ylim(0,8,5)

ax3.set_ylabel('MtCO2/yr', fontdict={'fontsize':16})
# ax3.set_ylim(0,600)
fig.get_figure().gca().set_title("")

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid()

fig.savefig('ammonia_feedstock_2307.jpg', bbox_inches='tight')

#### Methanol Final Energy (ALL)

In [ ]:
variable_list = [

'Final Energy|Non-Energy Use|Chemicals|Methanol|Gases',
'Final Energy|Non-Energy Use|Chemicals|Methanol|Solids|Biomass',
'Final Energy|Non-Energy Use|Chemicals|Methanol|Solids|Coal',
'Final Energy|Non-Energy Use|Chemicals|Methanol|Hydrogen',


]

variable_ccs = ["Carbon Sequestration|CCS|Industry|Biomass|Chemicals|Methanol",
                "Carbon Sequestration|CCS|Industry|Fossil|Chemicals|Methanol"]

df.aggregate(
    "Carbon Sequestration|CCS|Industry|Chemicals|Methanol", components=variable_ccs, append=True,
)

new_var_ccs = ["Carbon Sequestration|CCS|Industry|Chemicals|Methanol"]


df_graph_1 = df.copy()
df_graph_2 = df.copy()
df_graph_3 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)
df_graph_3.filter(variable= new_var_ccs, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
ax3 = ax2.twinx()
fig.tight_layout(pad=5)

pyam.run_control().update(
    {'color': {'variable': {
                 'Final Energy|Non-Energy Use|Chemicals|Methanol|Gases': 'slategrey',
                 'Final Energy|Non-Energy Use|Chemicals|Methanol|Hydrogen': 'lightblue',
                 'Final Energy|Non-Energy Use|Chemicals|Methanol|Solids|Biomass':'seagreen',
                 'Final Energy|Non-Energy Use|Chemicals|Methanol|Solids|Coal': 'darkslategrey'
    }}}
)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)
df_graph_3.plot.line(ax=ax3, color='black', linewidth=5)

ax2.legend(
     ['Coal',
      'Biomass', 
      'Electricity',
      'Gas',
     ],
     bbox_to_anchor=(1.3, 0.1),
     loc="lower right",
 )

ax1.set_title("", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,50,5)

ax2.set_title("", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
ax2.get_legend().remove()
ax2.set_ylim(0,50,5)

ax3.set_ylabel('MtCO2/yr', fontdict={'fontsize':16})
ax3.set_ylim(0,2500)
fig.get_figure().gca().set_title("")

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid()

fig.savefig('methanol_feedstock_2307.jpg', bbox_inches='tight')

### Iron and Steel

#### Final Energy

In [ ]:
# Iron and Steel

variable_list = [
    'Final Energy|Industry excl Non-Energy Use|Steel|Electricity',
    'Final Energy|Industry excl Non-Energy Use|Steel|Gases',
    'Final Energy|Industry excl Non-Energy Use|Steel|Heat',
    'Final Energy|Industry excl Non-Energy Use|Steel|Liquids|Biomass',
    'Final Energy|Industry excl Non-Energy Use|Steel|Liquids|Coal',
    'Final Energy|Industry excl Non-Energy Use|Steel|Liquids|Oil',
    'Final Energy|Industry excl Non-Energy Use|Steel|Solids|Biomass',
    'Final Energy|Industry excl Non-Energy Use|Steel|Solids|Coal', 
    'Final Energy|Industry excl Non-Energy Use|Steel|Hydrogen'
]


df_graph_1 = df.copy()
df_graph_2 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

# ax2.legend(
#      ['Coal',
#       'Gas', 
#       'Electricity',
#      ],
#      bbox_to_anchor=(1.4, 0.1),
#      loc="lower right",
#  )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})

#### Final Energy with CCS

In [ ]:
variable_list = [
    'Final Energy|Industry excl Non-Energy Use|Steel|Electricity',
    'Final Energy|Industry excl Non-Energy Use|Steel|Gases',
    'Final Energy|Industry excl Non-Energy Use|Steel|Heat',
    'Final Energy|Industry excl Non-Energy Use|Steel|Liquids|Biomass',
    'Final Energy|Industry excl Non-Energy Use|Steel|Liquids|Coal',
    'Final Energy|Industry excl Non-Energy Use|Steel|Liquids|Oil',
    'Final Energy|Industry excl Non-Energy Use|Steel|Solids|Biomass',
    'Final Energy|Industry excl Non-Energy Use|Steel|Solids|Coal', 
    'Final Energy|Industry excl Non-Energy Use|Steel|Hydrogen'
]

variable_ccs = ['Carbon Sequestration|CCS|Industry|Steel']

df_graph_1 = df.copy()
df_graph_2 = df.copy()
df_graph_3 = df.copy()
df_graph_4 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)
df_graph_3.filter(variable= variable_ccs, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)
df_graph_4.filter(variable= variable_ccs, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=7)
ax3 = ax2.twinx()
ax4 = ax1.twinx()

pyam.run_control().update(
{'color': {'variable': {
             'Final Energy|Industry excl Non-Energy Use|Steel|Hydrogen': 'brown',
             'Final Energy|Industry excl Non-Energy Use|Steel|Solids|Biomass': 'seagreen',
             'Final Energy|Industry excl Non-Energy Use|Steel|Solids|Coal': 'darkslategrey',
             'Final Energy|Industry excl Non-Energy Use|Steel|Liquids|Biomass': 'greenyellow',
             'Final Energy|Industry excl Non-Energy Use|Steel|Liquids|Oil': 'blue',
             'Final Energy|Industry excl Non-Energy Use|Steel|Liquids|Coal': 'mediumaquamarine',
             'Final Energy|Industry excl Non-Energy Use|Steel|Electricity': 'lightblue' ,
             'Final Energy|Industry excl Non-Energy Use|Steel|Gases': 'slategrey',
             'Final Energy|Industry excl Non-Energy Use|Steel|Heat': 'orange',
    

}}}
)

df_graph_1.plot.stack(ax=ax1, title = "")
df_graph_2.plot.stack(ax=ax2, title = "")
df_graph_3.plot.line(ax=ax3, color='black', linewidth=5, title = "")
df_graph_4.plot.line(ax=ax4, color='black', linewidth=5, title = "")


ax2.legend(
     ['Coal',
      'Biomass', 
      'Oil',
      'Methanol',
      'Ethanol',
      'Hydrogen',
      'Heat',
      'Gas',
      'Electricity'
     ],
     bbox_to_anchor=(1.7, 0.1),
     loc="lower right",
 )

ax3.legend(['CCS Use'],
     bbox_to_anchor=(1.7, 0.8),
     loc="lower right",)

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,35)


ax2.set_title("2 degrees", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
ax2.set_ylim(0,35)

ax3.set_ylabel('MtCO2/yr', fontdict={'fontsize':16})
ax3.set_ylim(0,850)

ax4.set_ylabel('MtCO2/yr', fontdict={'fontsize':16})
ax4.set_ylim(0,850)

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid()

# fig.get_figure().gca().set_title("")

fig.savefig('iron_and_steel_fe_2507.jpg', bbox_inches='tight')

#### Production

In [ ]:
variable_list = [
'Production|Primary|Steel',
'Production|Secondary|Steel'
]

df_graph_1 = df.copy()
df_graph_2 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

# ax2.legend(
#      ['Coal',
#       'Gas', 
#       'Electricity',
#      ],
#      bbox_to_anchor=(1.4, 0.1),
#      loc="lower right",
#  )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,2500,5)


ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
ax2.set_ylim(0,2500,5)

In [ ]:
# Scrap Use

variable_list = [
'Non-Collected Scrap|Steel', 
'Collected Scrap|Steel'

]

df.subtract('Total Scrap|Steel', 'Collected Scrap|Steel', 
        'Non-Collected Scrap|Steel',axis='variable', append = True)

df_graph_1 = df.copy()
df_graph_2 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

# ax2.legend(
#      ['Coal',
#       'Gas', 
#       'Electricity',
#      ],
#      bbox_to_anchor=(1.4, 0.1),
#      loc="lower right",
#  )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
# ax1.set_ylim(0,2500,5)


ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
# ax2.set_ylim(0,2500,5)

### Non-Metallic Minerals 

#### Final Energy

In [ ]:
variable_list = [

'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Electricity',
'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Gases',
'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Hydrogen',
'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Liquids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Liquids|Coal',
'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Liquids|Oil',
'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Solids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Solids|Coal'

]

variable_ccs = ['Carbon Sequestration|CCS|Industry|Industrial Processes|Non-Metallic Minerals']

df_graph_1 = df.copy()
df_graph_2 = df.copy()
df_graph_3 = df.copy()
df_graph_4 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)
df_graph_3.filter(variable= variable_ccs, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)
df_graph_4.filter(variable= variable_ccs, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=7)
ax3 = ax2.twinx()
ax4 = ax1.twinx()

pyam.run_control().update(
{'color': {'variable': {
             'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Hydrogen': 'brown',
             'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Solids|Biomass': 'seagreen',
             'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Solids|Coal': 'darkslategrey',
             'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Liquids|Biomass': 'greenyellow',
             'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Liquids|Oil': 'blue',
             'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Liquids|Coal': 'mediumaquamarine',
             'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Electricity': 'lightblue' ,
             'Final Energy|Industry excl Non-Energy Use|Non-Metallic Minerals|Gases': 'slategrey'
    

}}}
)

df_graph_1.plot.stack(ax=ax1, title = "")
df_graph_2.plot.stack(ax=ax2, title = "")
df_graph_3.plot.line(ax=ax3, color='black', linewidth=5, title = "")
df_graph_4.plot.line(ax=ax4, color='black', linewidth=5, title = "")


ax2.legend(
     ['Coal',
      'Biomass', 
      'Oil',
      'Methanol',
      'Ethanol',
      'Hydrogen',
      'Gas',
      'Electricity'
     ],
     bbox_to_anchor=(1.7, 0.1),
     loc="lower right",
 )

ax3.legend(['CCS Use'],
     bbox_to_anchor=(1.7, 0.8),
     loc="lower right",)

ax1.set_title("No Policy", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,22)


ax2.set_title("2 degrees", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
ax2.set_ylim(0,22)

ax3.set_ylabel('MtCO2/yr', fontdict={'fontsize':16})
ax3.set_ylim(0,1450)

ax4.set_ylabel('MtCO2/yr', fontdict={'fontsize':16})
ax4.set_ylim(0,1450)

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid()

# fig.get_figure().gca().set_title("")

fig.savefig('cement_final_energy_2507.jpg', bbox_inches='tight')

#### Production

In [ ]:
variable_list = [

'Production|Non-Metallic Minerals|Cement'

]

df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack()
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack()

### Non-Ferrous Metals 

#### Final Energy

In [ ]:
variable_list = [

'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Electricity',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Gases',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Heat',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Hydrogen',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Liquids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Liquids|Coal',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Liquids|Oil',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Solids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Non-Ferrous Metals|Solids|Coal'

]

df_graph_1 = df.copy()
df_graph_2 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

ax2.legend(
     ['Solids|Coal',
      'Solids|Biomass', 
      'Liquids|Oil',
      'Liquids|Coal',
      'Liquids|Biomass',
      'Hydrogen',
      'Heat',
      'Gas',
      'Electricity'
     ],
     bbox_to_anchor=(1.4, 0.1),
     loc="lower right",
 )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,10)

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
ax2.set_ylim(0,10)

#### Production

All the total scrap available is used both in baseline and 2degrees therefore no change in the secondary production.

In [ ]:
variable_list = [

'Production|Primary|Non-Ferrous Metals|Aluminium',
'Production|Secondary|Non-Ferrous Metals|Aluminium'

]

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name).plot.stack(ax=ax1)
df.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name).plot.stack(ax=ax2)

ax1.set_ylim(0,250)
ax2.set_ylim(0,250)

ax1.set_title("Scenario NoPolicy Non-Ferrous Metals", fontdict={'fontsize':16})
ax1.get_legend().remove()
ax2.set_title("Scenario 2degrees Non-Ferrous Metals", fontdict={'fontsize':16})

### Chemicals

#### Final Energy  (excl. Non-Energy Use)

In [ ]:
variable_list = [

'Final Energy|Industry excl Non-Energy Use|Chemicals|Electricity',
'Final Energy|Industry excl Non-Energy Use|Chemicals|Gases',
'Final Energy|Industry excl Non-Energy Use|Chemicals|Heat',
'Final Energy|Industry excl Non-Energy Use|Chemicals|Hydrogen',
'Final Energy|Industry excl Non-Energy Use|Chemicals|Liquids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Chemicals|Liquids|Coal',
'Final Energy|Industry excl Non-Energy Use|Chemicals|Liquids|Oil',
'Final Energy|Industry excl Non-Energy Use|Chemicals|Solids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Chemicals|Solids|Coal'
    
]

df_graph_1 = df.copy()
df_graph_2 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

ax2.legend(
     ['Solids|Coal',
      'Solids|Biomass', 
      'Liquids|Oil',
      'Liquids|Coal',
      'Liquids|Biomass',
      'Hydrogen',
      'Heat',
      'Gas',
      'Electricity'
     ],
     bbox_to_anchor=(1.4, 0.1),
     loc="lower right",
 )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,6,5)

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
ax2.set_ylim(0,6,5)

#### Production

In [ ]:
variable_list = [

'Production|Primary|Chemicals|Ammonia',
'Production|Primary|Chemicals|High Value Chemicals',
'Production|Primary|Chemicals|Methanol'
    
]

df_graph_1 = df.copy()
df_graph_2 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

ax2.legend(
     ['Methanol',
      'HVC',
      'Ammonia'
     ],
     bbox_to_anchor=(1.4, 0.1),
     loc="lower right",
 )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("Mt/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,2200,5)

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("Mt/yr", fontdict={'fontsize':16})
ax2.set_ylim(0,2200,5)

### Other Industry

In [ ]:
variable_list = [

'Final Energy|Industry excl Non-Energy Use|Other Sector|Electricity',
'Final Energy|Industry excl Non-Energy Use|Other Sector|Gases', 
'Final Energy|Industry excl Non-Energy Use|Other Sector|Heat', 
'Final Energy|Industry excl Non-Energy Use|Other Sector|Hydrogen',
'Final Energy|Industry excl Non-Energy Use|Other Sector|Liquids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Other Sector|Liquids|Oil',
'Final Energy|Industry excl Non-Energy Use|Other Sector|Liquids|Coal',
'Final Energy|Industry excl Non-Energy Use|Other Sector|Solar',
'Final Energy|Industry excl Non-Energy Use|Other Sector|Solids|Biomass',
'Final Energy|Industry excl Non-Energy Use|Other Sector|Solids|Coal'
    
]

df_graph_1 = df.copy()
df_graph_2 = df.copy()

pyam.run_control().update(
    {'color': {'variable': {'Final Energy|Industry excl Non-Energy Use|Other Sector|Solar': 'gold',
                 'Final Energy|Industry excl Non-Energy Use|Other Sector|Hydrogen': 'brown',
                 'Final Energy|Industry excl Non-Energy Use|Other Sector|Heat': 'olive',
                 'Final Energy|Industry excl Non-Energy Use|Other Sector|Solids|Biomass': 'seagreen',
                 'Final Energy|Industry excl Non-Energy Use|Other Sector|Solids|Coal': 'darkslategrey',
                 'Final Energy|Industry excl Non-Energy Use|Other Sector|Liquids|Biomass': 'greenyellow',
                 'Final Energy|Industry excl Non-Energy Use|Other Sector|Liquids|Coal': 'mediumaquamarine',
                 'Final Energy|Industry excl Non-Energy Use|Other Sector|Liquids|Oil': 'blue',
                 'Final Energy|Industry excl Non-Energy Use|Other Sector|Gases':'slategrey',
                 'Final Energy|Industry excl Non-Energy Use|Other Sector|Electricity':'lightblue',
    }}}
)

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

ax2.legend(
     ['Coal',
      'Biomass',
      'Solar',
      'Oil',
      'Ethanol',
      'Hydrogen',
      'Heat',
      'Gas',
      'Electricity'
     ],
     bbox_to_anchor=(1.4, 0.1),
     loc="lower right",
 )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("EJ/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
# ax1.set_ylim(0,6,5)

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("EJ/yr", fontdict={'fontsize':16})
# ax2.set_ylim(0,6,5)

fig.savefig('other_sector_2307', bbox_inches='tight')

### Power Sector

#### Material Demand

#### Scrap Release

#### Stocks

In [ ]:
# The excel file is generated by Historical Power Sector Stock Reporting-Fixed_Version.ipynb

df_stock_1 = pd.read_excel('MESSAGEix-Materials_baseline_DEFAULT_update_2207_power_sector_material.xlsx')
df_stock_2 = pd.read_excel('MESSAGEix-Materials_2degrees_2207_2025_macro_power_sector_material.xlsx')
years = [2015,2020,2025,2030,2035,2040,2045,2050,2055,2060,2070]

df_stock_graph_1 = pyam.IamDataFrame(data=df_stock_1)
df_stock_graph_2 = pyam.IamDataFrame(data=df_stock_2)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=5)

df_stock_graph_1.filter(variable="Material Stock|*", region="R12_GLB", year = years).plot.bar(ax = ax1, stacked=True)
df_stock_graph_2.filter(variable="Material Stock|*", region="R12_GLB", year = years).plot.bar(ax = ax2, stacked=True)

ax2.legend(
     ['Aluminum',
      'Cement', 
      'Steel',
     ],
     bbox_to_anchor=(1.4, 0.1),
     loc="lower right",
 )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("Mt",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,7000)

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("Mt", fontdict={'fontsize':16})
ax2.set_ylim(0,7000)

# fig.suptitle('Power Sector Material Stocks, Global',fontsize=15)

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid() 

fig.savefig('power_Sector_stock_bymaterials_2507.jpg', bbox_inches='tight')

In [ ]:
# The excel file is generated by Historical Power Sector Stock Reporting-Fixed_Version.ipynb
# Adjust the units to TW

df_stock_1 = pd.read_excel('MESSAGEix-Materials_baseline_DEFAULT_update_2207_detailed_output4.xlsx')
df_stock_2 = pd.read_excel('MESSAGEix-Materials_2degrees_2207_2025_macro_detailed_output4.xlsx')

df_stock_1 = df_stock_1[((df_stock_1['year_act']>=2015) & (df_stock_1['node_loc']=='R12_GLB') & 
                        (df_stock_1['year_act']<=2070))]
df_stock_2 = df_stock_2[((df_stock_2['year_act']>=2015) & (df_stock_2['node_loc']== 'R12_GLB') &
                        (df_stock_1['year_act']<2070))]

df_stock_1.drop(['commodity', 'material_stock','node_dest','level','node_loc'], axis = 1, inplace = True)
df_stock_1 = df_stock_1.drop_duplicates()
df_stock_1 = pd.pivot_table(df_stock_1, values = 'capacity', index = ['year_act'], columns = ['technology'])

df_stock_2.drop(['commodity', 'material_stock','node_dest','level','node_loc'], axis = 1, inplace = True)
df_stock_2 = df_stock_2.drop_duplicates()
df_stock_2 = pd.pivot_table(df_stock_2, values = 'capacity', index = ['year_act'], columns = ['technology'])



fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10,5))
fig.tight_layout(pad=5)

color_map = {
      'Bioenergy': 'mediumseagreen',
      'Bioenergy CCS': 'lightgreen',
      'Coal': 'black', 
      'Coal CCS': 'slategrey',
      'Solar CSP': 'orange',
      'Oil': 'darkolivegreen',
      'Gas': 'grey',
      'Gas CCS': 'lightgrey',
      'Hydropower': 'deepskyblue',
      'Nuclear': 'maroon',
      'Solar PV': 'yellow',
      'Wind Onshore': 'cornflowerblue',
      'Wind Offshore': 'lightsteelblue'
}

# color_map = {
#       'bio_istig': 'black',
#       'bio_istig_ccs': 'lightgray',
#       'bio_ppl': 'lightcoral',
#       'coal_adv': 'maroon', 
#       'coal_adv_ccs': 'coral',
#       'coal_ppl': 'darkorange',
#       'coal_ppl_u': 'orange',
#       'csp_sm1_ppl': 'darkgoldenrod',
#       'csp_sm3_ppl': 'olive',
#       'foil_ppl': 'yellowgreen',
#       'gas_cc': 'lawngreen',
#       'gas_cc_ccs': 'lightgreen',
#       'gas_ct': 'darkgreen',
#       'gas_ppl': 'mediumseagreen',
#       'hydro_hc': 'mediumturquoise', 
#       'hydro_lc': 'darkslategray',
#       'igcc': 'skyblue',
#       'igcc_ccs': 'dodgerblue',
#       'loil_cc': 'darkblue',
#       'loil_ppl': 'slateblue',
#       'nuc_hc': 'darkviolet',
#       'nuc_lc': 'violet',
#       'solar_pv_ppl': 'crimson',
#       'wind_ppf': 'fuchsia',
#       'wind_ppl': 'dimgrey'}

df_stock_1.plot.bar(ax = ax1, stacked = True, color = color_map)
df_stock_2.plot.bar(ax = ax2, stacked = True, color = color_map)

ax2.legend(
     bbox_to_anchor=(1.6, 0.1),
     loc="lower right",
 )

# ax2.legend(
#      ['Advanced biomass',
#       'Advanced biomass CCS',
#       'Biomass',
#       'Advanced coal', 
#       'Advanced coal CCS',
#       'Coal',
#       'Coal wo abatement',
#       'CSP-solar multiple 1',
#       'CSP-solar multiple 3',
#       'Fuel oil',
#       'Gas combined cycle',
#       'Gas combined cycle CCS',
#       'Gas combustion tirbune',
#       'Gas',
#       'Hydro-high cost',
#       'Hydro-low cost',
#       'IGCC',
#       'IGCC CCS',
#       'Light oil combined cycle',
#       'Light oil',
#       'Nuclear-high cost',
#       'Nuclear-low cost',
#       'Solar PV',
#       'Wind offshore',
#       'Wind onshore',
#      ],
#      bbox_to_anchor=(1.5, 0.1),
#      loc="lower right",
#  )

ax1.set_title("", fontdict={'fontsize':16})
ax1.set_xlabel("", fontdict={'fontsize':16})
ax1.set_ylabel("TW",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,41)

ax2.set_title("", fontdict={'fontsize':16})
ax2.set_xlabel("", fontdict={'fontsize':16})
ax2.set_ylabel("TW", fontdict={'fontsize':16})
ax2.set_ylim(0,41)

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid()

fig.savefig('power_Sector_stock_bycapacity_2507.jpg', bbox_inches='tight')

### CCS

#### Total Industry CCS Use

In [ ]:
variable_list = [

'Carbon Sequestration|CCS|Industry|Biomass|Chemicals', 
'Carbon Sequestration|CCS|Industry|Fossil|Chemicals', 
'Carbon Sequestration|CCS|Industry|Industrial Processes|Non-Metallic Minerals'

]

df_graph_1 = df.copy()
df_graph_2 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

# ax2.legend(
#      ['Methanol',
#       'Liquids|Oil', 
#       'Liquids|Gas',
#       'Liquids|Biomass',
#      ],
#      bbox_to_anchor=(1.4, 0.1),
#      loc="lower right",
#  )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("Mt CO2/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()
ax1.set_ylim(0,3000,5)

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("Mt CO2/yr", fontdict={'fontsize':16})
ax2.set_ylim(0,3000,5)

#### Cement Industry CCS Use

In [ ]:
df.filter(variable='Carbon Sequestration|CCS|Industrial Processes', region='GLB region (R12)').plot()

In [ ]:
from message_ix.reporting import Reporter
from ixmp.reporting import configure

rep1 = Reporter.from_scenario(scen1)
configure(units={"replace": {"-": ""}})
df1 = rep1.get("message::default")

rep2 = Reporter.from_scenario(scen2)
configure(units={"replace": {"-": ""}})
df2 = rep2.get("message::default")

df_ccs = pyam.concat([df1,df2])

variable_list = [
'emis|CO2|biomass_NH3_ccs|*',
'emis|CO2|gas_NH3_ccs|*',
'emis|CO2|coal_NH3_ccs|*',
'emis|CO2|fueloil_NH3_ccs|*',
'emis|CO2|fueloil_NH3_ccs|*',
'emis|CO2|clinker_dry_ccs_cement|*',
'emis|CO2|clinker_wet_ccs_cement|*'   
]

df_ccs.aggregate_region(variable_list, append = True)

In [ ]:
df_graph_1 = df_ccs.copy()
df_graph_2 = df_ccs.copy()

df_graph_1.convert_unit('Mt / a', to='Mt/yr', factor=-1, inplace=True)
df_graph_2.convert_unit('', to='Mt/yr', factor=-1, inplace=True)

# pyam.run_control().update(
#     {'color': {'variable': {'Final Energy|Industry|Solar': 'slategrey',
#                  'Final Energy|Indsutry|Hydrogen': 'brown',
#                  'Final Energy|Industry|Heat': 'deepskyblue',
#                  'Final Energy|Industry|Solids|Biomass': 'cadetblue',
#                  'Final Energy|Industry|Solids|Coal': 'orange',
#                  'Final Energy|Industry|Liquids|Biomass': 'darkcyan',
#                  'Final Energy|Industry|Liquids|Coal': 'darkslategrey',
#                  'Final Energy|Industry|Liquids|Gas': 'lightseagreen',
#                  'Final Energy|Industry|Liquids|Oil': 'blue',
#                  'Final Energy|Industry|Geothermal': 'mediumaquamarine',
#                  'Final Energy|Industry|Gases':'grey',
#                  'Final Energy|Industry|Electricity':'seagreen',
#                 'Final Energy|Industry|Other':'darkgreen'    
#     }}}
# )

df_graph_1.filter(variable= variable_list, region='World', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='World', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

ax2.legend(
     ['Gas NH3',
      'Fueloil NH3', 
      'Coal NH3',
      'Clinker Wet Cement',
      'Clinker Dry Cement',
      'Biomass NH3',
     ],
     bbox_to_anchor=(1.4, 0.1),
     loc="lower right",
 )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("MtCO2",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("MtCO2", fontdict={'fontsize':16})

ax1.xaxis.grid() 
ax1.yaxis.grid() 
ax2.yaxis.grid() 
ax2.xaxis.grid() 

#### Chemicals Industry CCS Use

In [ ]:
variable_list = [

'Carbon Sequestration|CCS|Industry|Biomass|Chemicals',
'Carbon Sequestration|CCS|Industry|Fossil|Chemicals'

]

df_graph_1 = df.copy()
df_graph_2 = df.copy()

df_graph_1.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen1_name, inplace = True)
df_graph_2.filter(variable= variable_list, region='GLB region (R12)', model = model1_name, scenario = scen2_name, inplace = True)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15,7.5))
fig.tight_layout(pad=10.0)

df_graph_1.plot.stack(ax=ax1)
df_graph_2.plot.stack(ax=ax2)

# ax2.legend(
#      ['Methanol',
#       'Liquids|Oil', 
#       'Liquids|Gas',
#       'Liquids|Biomass',
#      ],
#      bbox_to_anchor=(1.4, 0.1),
#      loc="lower right",
#  )

ax1.set_title("NoPolicy", fontdict={'fontsize':16})
ax1.set_xlabel("Year", fontdict={'fontsize':16})
ax1.set_ylabel("Mt CO2/yr",fontdict={'fontsize':16})
ax1.get_legend().remove()

ax2.set_title("2degrees", fontdict={'fontsize':16})
ax2.set_xlabel("Year", fontdict={'fontsize':16})
ax2.set_ylabel("Mt CO2/yr", fontdict={'fontsize':16})

In [ ]:
# FINAL ENERGY

var_steel = ["Final Energy|Industry|Steel"]
var_alu = ["Final Energy|Industry|Non-Ferrous Metals"]
var_chem = ["Final Energy|Industry|Chemicals"]
var_cement = ["Final Energy|Industry|Non-Metallic Minerals"]

fig, axs = plt.subplots(3,4, figsize=(7,10), layout='tight')

df_scenario_data_alu = timeseries_final.copy()
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["variable"].isin(var_alu)]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["region"]=="GLB region (R12)"]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["model"]==model1_name]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["scenario"]==scen1_name]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["year"]==2020]
df_scenario_data_alu["scenario"] = "MESSAGE, 2020"

df_scenario_data_steel = timeseries_final.copy()
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["variable"].isin(var_steel)]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["region"]=="GLB region (R12)"]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["model"]==model1_name]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["scenario"]==scen1_name]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["year"]==2020]
df_scenario_data_steel["scenario"] = "MESSAGE, 2020"

df_scenario_data_cement = timeseries_final.copy()
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["variable"].isin(var_cement)]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["region"]=="GLB region (R12)"]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["model"]==model1_name]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["scenario"]==scen1_name]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["year"]==2020]
df_scenario_data_cement["scenario"] = "MESSAGE, 2020"

df_scenario_data_chem = timeseries_final.copy()
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["variable"].isin(var_chem)]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["region"]=="GLB region (R12)"]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["model"]==model1_name]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["scenario"]==scen1_name]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["year"]==2020]
df_scenario_data_chem["scenario"] = "MESSAGE, 2020"

df_iea_final_energy_steel = pd.DataFrame([
    ['GLB region (R12)','Final Energy|Industry|Steel','EJ/yr', 2020, 22,'MESSAGEix-Materials','Statistics'],
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_iea_final_energy_alu = pd.DataFrame([
    ['GLB region (R12)','Final Energy|Industry|Non-Ferrous Metals','EJ/yr', 2020, 4.77, 'MESSAGEix-Materials', 'Statistics'],
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_iea_final_energy_cement = pd.DataFrame([
    ['GLB region (R12)',"Final Energy|Industry|Non-Metallic Minerals",'EJ/yr',2020, 15.7, 'MESSAGEix-Materials', 'Statistics'],
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_iea_final_energy_chem = pd.DataFrame([
    ['GLB region (R12)',"Final Energy|Industry|Chemicals", 'EJ/yr',2020, 37.3, 'MESSAGEix-Materials', 'Statistics']
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_final_alu = pd.concat([df_iea_final_energy_alu,df_scenario_data_alu])
df_final_steel = pd.concat([df_iea_final_energy_steel,df_scenario_data_steel])
df_final_cement = pd.concat([df_iea_final_energy_cement,df_scenario_data_cement])
df_final_chem = pd.concat([df_iea_final_energy_chem, df_scenario_data_chem])

df_final_alu = pyam.IamDataFrame(df_final_alu)
df_final_steel = pyam.IamDataFrame(df_final_steel)
df_final_cement = pyam.IamDataFrame(df_final_cement)
df_final_chem = pyam.IamDataFrame(df_final_chem)

df_final_alu.plot.bar(ax = axs[0,0], x= "scenario", stacked=False, title = "Aluminum")
df_final_steel.plot.bar(ax = axs[0,1], x= "scenario", stacked=False, title = "Steel", )
df_final_chem.plot.bar(ax = axs[0,2], x= "scenario", stacked=False, title = "Chemicals")
df_final_cement.plot.bar(ax = axs[0,3], x= "scenario", stacked=False, title = "Cement")

axs[0,0].set_ylim(0,40,5)
axs[0,1].set_ylim(0,40,5)
axs[0,2].set_ylim(0,40,5)
axs[0,3].set_ylim(0,40,5)

axs[0,0].get_legend().remove()
axs[0,1].get_legend().remove()
axs[0,2].get_legend().remove()
axs[0,3].get_legend().remove()

axs[0,1].set_ylabel(" ")
axs[0,2].set_ylabel(" ")
axs[0,3].set_ylabel(" ")

axs[0,1].get_yaxis().set_visible(False)
axs[0,2].get_yaxis().set_visible(False)
axs[0,3].get_yaxis().set_visible(False)

axs[0,0].set_xlabel(" ")
axs[0,1].set_xlabel(" ")
axs[0,2].set_xlabel(" ")
axs[0,3].set_xlabel(" ")


# PRODUCTION

var_steel = ["Production|Steel"]
var_alu = ["Production|Non-Ferrous Metals|Aluminium"]
var_chem = ["Production|Chemicals"]
var_cement = ["Production|Non-Metallic Minerals|Cement"]

df_scenario_data_alu = timeseries_final.copy()
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["variable"].isin(var_alu)]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["region"]=="GLB region (R12)"]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["model"]==model1_name]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["scenario"]==scen1_name]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["year"]==2020]
df_scenario_data_alu["scenario"] = "MESSAGE, 2020"

df_scenario_data_steel = timeseries_final.copy()
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["variable"].isin(var_steel)]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["region"]=="GLB region (R12)"]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["model"]==model1_name]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["scenario"]==scen1_name]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["year"]==2020]
df_scenario_data_steel["scenario"] = "MESSAGE, 2020"

df_scenario_data_cement = timeseries_final.copy()
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["variable"].isin(var_cement)]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["region"]=="GLB region (R12)"]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["model"]==model1_name]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["scenario"]==scen1_name]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["year"]==2020]
df_scenario_data_cement["scenario"] = "MESSAGE, 2020"

df_scenario_data_chem = timeseries_final.copy()
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["variable"].isin(var_chem)]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["region"]=="GLB region (R12)"]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["model"]==model1_name]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["scenario"]==scen1_name]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["year"]==2020]
df_scenario_data_chem["scenario"] = "MESSAGE, 2020"

df_iea_final_energy_steel = pd.DataFrame([
    ['GLB region (R12)','Production|Steel','Mt/yr', 2020, 1880,'MESSAGEix-Materials','Statistics'],
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_iea_final_energy_alu = pd.DataFrame([
    ['GLB region (R12)',"Production|Non-Ferrous Metals|Aluminium",'Mt/yr', 2020, 94.341, 'MESSAGEix-Materials', 'Statistics'],
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_iea_final_energy_cement = pd.DataFrame([
    ['GLB region (R12)',"Production|Non-Metallic Minerals|Cement",'Mt/yr',2020, 4190, 'MESSAGEix-Materials', 'Statistics'],
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_iea_final_energy_chem = pd.DataFrame([
    ['GLB region (R12)',"Production|Chemicals", 'Mt/yr',2020, 543.5, 'MESSAGEix-Materials', 'Statistics']
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_final_alu = pd.concat([df_iea_final_energy_alu,df_scenario_data_alu])
df_final_steel = pd.concat([df_iea_final_energy_steel,df_scenario_data_steel])
df_final_cement = pd.concat([df_iea_final_energy_cement,df_scenario_data_cement])
df_final_chem = pd.concat([df_iea_final_energy_chem, df_scenario_data_chem])

df_final_alu = pyam.IamDataFrame(df_final_alu)
df_final_steel = pyam.IamDataFrame(df_final_steel)
df_final_cement = pyam.IamDataFrame(df_final_cement)
df_final_chem = pyam.IamDataFrame(df_final_chem)

df_final_alu.plot.bar(ax = axs[1,0], x= "scenario", stacked=False, title = "")
df_final_steel.plot.bar(ax = axs[1,1], x= "scenario", stacked=False, title = "")
df_final_chem.plot.bar(ax = axs[1,2], x= "scenario", stacked=False, title = "")
df_final_cement.plot.bar(ax = axs[1,3], x= "scenario", stacked=False, title = "")

axs[1,0].set_ylim(0,4500,10)
axs[1,1].set_ylim(0,4500,10)
axs[1,2].set_ylim(0,4500,10)
axs[1,3].set_ylim(0,4500,10)

axs[1,0].get_legend().remove()
axs[1,1].get_legend().remove()
axs[1,2].get_legend().remove()
axs[1,3].get_legend().remove()

axs[1,1].set_ylabel(" ")
axs[1,2].set_ylabel(" ")
axs[1,3].set_ylabel(" ")

axs[1,1].get_yaxis().set_visible(False)
axs[1,2].get_yaxis().set_visible(False)
axs[1,3].get_yaxis().set_visible(False)

axs[1,0].set_xlabel(" ")
axs[1,1].set_xlabel(" ")
axs[1,2].set_xlabel(" ")
axs[1,3].set_xlabel(" ")

# EMISSIONS

var_steel = ["Emissions|CO2|Energy|Demand|Industry|Steel"]
var_alu = ['Emissions|CO2|Energy|Demand|Industry|Non-Ferrous Metals', 
                  'Emissions|CO2|Industrial Processes|Non-Ferrous Metals']
var_chem = ["Emissions|CO2|Energy|Demand|Industry|Chemicals"]
var_cement = ['Emissions|CO2|Energy|Demand|Industry|Non-Metallic Minerals|Cement', 
                'Emissions|CO2|Industrial Processes|Non-Metallic Minerals|Cement']

df_scenario_data_alu = timeseries_final.copy()
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["variable"].isin(var_alu)]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["region"]=="GLB region (R12)"]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["model"]==model1_name]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["scenario"]==scen1_name]
df_scenario_data_alu = df_scenario_data_alu[df_scenario_data_alu["year"]==2020]
df_scenario_data_alu["scenario"] = "MESSAGE, 2020"

df_scenario_data_steel = timeseries_final.copy()
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["variable"].isin(var_steel)]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["region"]=="GLB region (R12)"]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["model"]==model1_name]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["scenario"]==scen1_name]
df_scenario_data_steel = df_scenario_data_steel[df_scenario_data_steel["year"]==2020]
df_scenario_data_steel["scenario"] = "MESSAGE, 2020"

df_scenario_data_cement = timeseries_final.copy()
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["variable"].isin(var_cement)]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["region"]=="GLB region (R12)"]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["model"]==model1_name]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["scenario"]==scen1_name]
df_scenario_data_cement = df_scenario_data_cement[df_scenario_data_cement["year"]==2020]
df_scenario_data_cement["scenario"] = "MESSAGE, 2020"

df_scenario_data_chem = timeseries_final.copy()
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["variable"].isin(var_chem)]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["region"]=="GLB region (R12)"]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["model"]==model1_name]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["scenario"]==scen1_name]
df_scenario_data_chem = df_scenario_data_chem[df_scenario_data_chem["year"]==2020]
df_scenario_data_chem["scenario"] = "MESSAGE, 2020"

df_iea_final_energy_steel = pd.DataFrame([
    ['GLB region (R12)',"Emissions|CO2|Energy|Demand|Industry|Steel",'Mt/yr', 2020, 2100,'MESSAGEix-Materials','Statistics'],
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_iea_final_energy_alu = pd.DataFrame([
    ['GLB region (R12)',"Emissions|CO2|Industry|Non-Ferrous Metals|Aluminium",'Mt/yr', 2020, 200, 'MESSAGEix-Materials', 'Statistics'],
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_iea_final_energy_cement = pd.DataFrame([
    ['GLB region (R12)',"Emissions|CO2|Industry|Non-Metallic Minerals|Cement",'Mt/yr',2020, 2300, 'MESSAGEix-Materials', 'Statistics'],
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_iea_final_energy_chem = pd.DataFrame([
    ['GLB region (R12)',"Emissions|CO2|Energy|Demand|Industry|Chemicals", 'Mt/yr',2020, 845, 'MESSAGEix-Materials', 'Statistics']
],
    columns=['region', 'variable', 'unit', 'year', 'value', 'model','scenario'],
)

df_final_alu = pd.concat([df_iea_final_energy_alu,df_scenario_data_alu])
df_final_steel = pd.concat([df_iea_final_energy_steel,df_scenario_data_steel])
df_final_cement = pd.concat([df_iea_final_energy_cement,df_scenario_data_cement])
df_final_chem = pd.concat([df_iea_final_energy_chem, df_scenario_data_chem])

df_final_alu = pyam.IamDataFrame(df_final_alu)
df_final_alu.aggregate(
    "Emissions|CO2|Industry|Non-Ferrous Metals|Aluminium", components=var_alu, append=True,
)
df_final_alu.filter(variable=["Emissions|CO2|Industry|Non-Ferrous Metals|Aluminium"], inplace = True)

df_final_steel = pyam.IamDataFrame(df_final_steel)
df_final_cement = pyam.IamDataFrame(df_final_cement)
df_final_cement.aggregate(
    "Emissions|CO2|Industry|Non-Metallic Minerals|Cement", components=var_cement, append=True,
)
df_final_cement.filter(variable=["Emissions|CO2|Industry|Non-Metallic Minerals|Cement"], inplace = True)

df_final_chem = pyam.IamDataFrame(df_final_chem)

df_final_alu.plot.bar(ax = axs[2,0], x= "scenario", stacked=False, title = "")
df_final_steel.plot.bar(ax = axs[2,1], x= "scenario", stacked=False, title = "")
df_final_chem.plot.bar(ax = axs[2,2], x= "scenario", stacked=False, title = "")
df_final_cement.plot.bar(ax = axs[2,3], x= "scenario", stacked=False, title = "")

axs[2,0].set_ylim(0,3100,5)
axs[2,1].set_ylim(0,3100,5)
axs[2,2].set_ylim(0,3100,5)
axs[2,3].set_ylim(0,3100,5)

axs[2,0].get_legend().remove()
axs[2,1].get_legend().remove()
axs[2,2].get_legend().remove()
axs[2,3].get_legend().remove()

axs[0,0].set_ylabel("Final Energy (EJ/yr)")
axs[1,0].set_ylabel("Production (Mt)")
axs[2,0].set_ylabel("CO2 Emissions (MtCO2/yr)")
axs[2,1].set_ylabel(" ")
axs[2,2].set_ylabel(" ")
axs[2,3].set_ylabel(" ")

axs[2,1].get_yaxis().set_visible(False)
axs[2,2].get_yaxis().set_visible(False)
axs[2,3].get_yaxis().set_visible(False)

axs[2,0].set_xlabel(" ")
axs[2,1].set_xlabel(" ")
axs[2,2].set_xlabel(" ")
axs[2,3].set_xlabel(" ")

axs[1,0].xaxis.set_ticklabels([])
axs[1,1].xaxis.set_ticklabels([])
axs[1,2].xaxis.set_ticklabels([])
axs[1,3].xaxis.set_ticklabels([])

axs[0,0].xaxis.set_ticklabels([])
axs[0,1].xaxis.set_ticklabels([])
axs[0,2].xaxis.set_ticklabels([])
axs[0,3].xaxis.set_ticklabels([])